**GAZP**

* GAZP Github, Download the repo from the link: https://github.com/vzhong/gazp


*   Follow the steps as given in the github repository to load Glove, cosql data, database and BERT.


*  Follow the Colab file to run the gazp: https://colab.research.google.com/drive/1mmFCurN_PTVlwLj7EaUDPyXodp2Pqzvv?usp=sharing

# Setup

In [ ]:
import traceback, torch
import os, sys, glob, tqdm
import random, json, re
import argparse, itertools
from collections import defaultdict, Counter
from google.colab import drive

drive.mount('/content/drive', force_remount=True)

Mounted at /content/drive


In [ ]:
gazp_basepath = "/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp"

In [ ]:
#!mkdir "/content/drive/My Drive/NL2SQL/Models/gazp/cache/bert"

In [ ]:
# !wget https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased-vocab.txt -O "/content/drive/My Drive/NL2SQL/Models/gazp/cache/bert/vocab.txt"
# !wget https://s3.amazonaws.com/models.huggingface.co/bert/distilbert-base-uncased-pytorch_model.bin -O "/content/drive/My Drive/NL2SQL/Models/gazp/cache/bert/pytorch_model.bin"
# !wget https://s3.amazonaws.com/models.huggingface.co/bert/distilbert-base-uncased-config.json -O "/content/drive/My Drive/NL2SQL/Models/gazp/cache/bert/config.json"

In [ ]:
import nltk
from nltk.stem.porter import PorterStemmer
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [ ]:
sys.path.append(gazp_basepath)

In [ ]:
!pip uninstall transformers

In [ ]:
!pip install pysqlite3
!pip install embeddings
!pip install vocab
!pip install transformers==3.0.2
!pip install loguru
# !pip install converter

     |████████████████████████████████| 40kB 5.0MB/s 
  Created wheel for pysqlite3: filename=pysqlite3-0.4.6-cp37-cp37m-linux_x86_64.whl size=132562 sha256=930782278df29796f15993799d3302be6bf6147722bb056230a87d77d8b2f10b
  Stored in directory: /root/.cache/pip/wheels/52/bd/85/9f859f07cb153f4d7e3ed094b821fb08b85935c2522c3bd9d4
Successfully built pysqlite3
     |████████████████████████████████| 778kB 13.7MB/s 
     |████████████████████████████████| 1.2MB 22.8MB/s 
     |████████████████████████████████| 901kB 42.5MB/s 
     |████████████████████████████████| 3.0MB 50.7MB/s 
     |████████████████████████████████| 61kB 6.5MB/s 


In [ ]:
import sqlite3, embeddings as E, vocab as Vocab, transformers

In [ ]:
!ls -ltr "/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp"

lrw------- 1 root root 0 Jul  5 05:14 '/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp' -> /content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp


In [ ]:
%cd "/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp"

In [ ]:
!pwd

/content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp


In [ ]:
os.path.abspath(os.getcwd())

'/content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp'

# Preprocessing

In [ ]:
!python preprocess_nl2sql_cosql.py

Streaming output truncated to the last 5000 lines.
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
'from' not found
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/voter_1/voter_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/voter_1/voter_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/voter_1/voter_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/voter_1/voter_1.sqlite
/content/dri

In [ ]:
!python preprocess_sql2nl_cosql.py

Streaming output truncated to the last 5000 lines.
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/databas

In [ ]:
!python preprocess_nl2sql_cosql.py

Streaming output truncated to the last 5000 lines.
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/dog_kennels/dog_kennels.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/dog_kennels/dog_kennels.sqlite
preprocess dev:  19% 56/293 [00:07<00:29,  7.99it/s]/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/world_1/world_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gaz

In [ ]:
!python preprocess_sql2nl_cosql.py

Streaming output truncated to the last 5000 lines.
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/epinions_1/epinions_1.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/databas

# Training NL2SQL

In [ ]:
# from transformers import BertTokenizer, BertModel
# tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
# model = BertModel.from_pretrained('bert-base-uncased')

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [ ]:
# model.save_pretrained("/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/cache/bert")
# tokenizer.save_pretrained("/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/cache/bert")
# tokenizer.save_vocabulary("/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/cache/bert")

('/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/cache/bert/vocab.txt',)

In [ ]:
!ls -ltr

total 225
-rw------- 1 root root  2967 Feb  1 12:49 utils.py
-rw------- 1 root root  3378 Feb  1 12:49 timed_execute.py
-rw------- 1 root root  4830 Feb  1 12:49 README.md
-rw------- 1 root root  8291 Feb  1 12:49 preprocess_sql2nl_sparc.py
-rw------- 1 root root  9725 Feb  1 12:49 preprocess_nl2sql_sparc.py
-rw------- 1 root root 14555 Feb  1 12:49 preprocess_nl2sql_novalue.py
-rw------- 1 root root   967 Feb  1 12:49 pred.sh
-rw------- 1 root root  3435 Feb  1 12:49 predict_sparc.py
-rw------- 1 root root  3652 Feb  1 12:49 predict.py
-rw------- 1 root root  1069 Feb  1 12:49 LICENSE
-rw------- 1 root root 17672 Feb  1 12:49 editsql_postprocess.py
-rw------- 1 root root   379 Feb  1 12:49 download.sh
-rw------- 1 root root   234 Feb  1 12:49 download_nltk.py
-rw------- 1 root root  4083 Feb  1 12:49 dataset.py
-rw------- 1 root root 28125 Feb  1 12:49 bleu.py
drwx------ 3 root root  4096 May 10 12:35 eval_scripts
drwx------ 2 root root  4096 May 10 12:35 adapt
drwx------ 5 root root 

In [ ]:
!python train.py --dataset cosql --name r1 --keep_values --model nl2sql

Streaming output truncated to the last 5000 lines.
train:   9% 53/623 [00:51<08:55,  1.06it/s]
train:   9% 54/623 [00:52<08:51,  1.07it/s]
train:   9% 55/623 [00:53<09:29,  1.00s/it]
train:   9% 56/623 [00:54<09:06,  1.04it/s]
train:   9% 57/623 [00:55<09:02,  1.04it/s]
train:   9% 58/623 [00:56<08:48,  1.07it/s]
train:   9% 59/623 [00:57<08:53,  1.06it/s]
train:  10% 60/623 [00:58<08:57,  1.05it/s]
train:  10% 61/623 [00:59<09:21,  1.00it/s]
train:  10% 62/623 [01:00<09:13,  1.01it/s]
train:  10% 63/623 [01:01<09:08,  1.02it/s]
train:  10% 64/623 [01:02<08:43,  1.07it/s]
train:  10% 65/623 [01:03<08:23,  1.11it/s]
train:  11% 66/623 [01:04<08:30,  1.09it/s]
train:  11% 67/623 [01:05<08:41,  1.07it/s]
train:  11% 68/623 [01:06<08:54,  1.04it/s]
train:  11% 69/623 [01:07<08:47,  1.05it/s]
train:  11% 70/623 [01:07<08:26,  1.09it/s]
train:  11% 71/623 [01:08<08:13,  1.12it/s]
train:  12% 72/623 [01:09<08:10,  1.12it/s]
train:  12% 73/623 [01:10<08:22,  1.09it/s]
train:  12% 74/623 [01:11

# Training SQL2NL

In [ ]:
!pwd

/content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp


In [ ]:
!ls -ltr

total 225
-rw------- 1 root root  2967 Feb  1 12:49 utils.py
-rw------- 1 root root  3378 Feb  1 12:49 timed_execute.py
-rw------- 1 root root  4830 Feb  1 12:49 README.md
-rw------- 1 root root  8291 Feb  1 12:49 preprocess_sql2nl_sparc.py
-rw------- 1 root root  9725 Feb  1 12:49 preprocess_nl2sql_sparc.py
-rw------- 1 root root 14555 Feb  1 12:49 preprocess_nl2sql_novalue.py
-rw------- 1 root root   967 Feb  1 12:49 pred.sh
-rw------- 1 root root  3435 Feb  1 12:49 predict_sparc.py
-rw------- 1 root root  3652 Feb  1 12:49 predict.py
-rw------- 1 root root  1069 Feb  1 12:49 LICENSE
-rw------- 1 root root 17672 Feb  1 12:49 editsql_postprocess.py
-rw------- 1 root root   379 Feb  1 12:49 download.sh
-rw------- 1 root root   234 Feb  1 12:49 download_nltk.py
-rw------- 1 root root  4083 Feb  1 12:49 dataset.py
-rw------- 1 root root 28125 Feb  1 12:49 bleu.py
drwx------ 2 root root  4096 May 10 12:35 eval_scripts
drwx------ 2 root root  4096 May 10 12:35 adapt
drwx------ 2 root root 

In [ ]:
!python train.py --dataset cosql --name r1 --model sql2nl --fparser "/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/exp/nl2sql/r1/best.tar" --fcache "/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/cache/data_sql2nl_sparc_cosql.pt"

Streaming output truncated to the last 5000 lines.
official eval:   6% 65/1006 [00:29<07:12,  2.17it/s]/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/flight_2/flight_2.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/flight_2/flight_2.sqlite

official eval:   7% 66/1006 [00:30<07:13,  2.17it/s]/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/flight_2/flight_2.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/flight_2/flight_2.sqlite

official eval:   7% 67/1006 [00:30<07:09,  2.19it/s]/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/singer/singer.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/singer/singer.sqlite

official eval:   7% 68/1006 [00:31<07:09,  2.18it/s]/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/singer/singer.sqlite
db: /content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/data/database/singer/singer.sqlite

o

# Generate Data

In [ ]:
!ls -ltr gen

total 212728
-rw------- 1 root root 11127663 Jun  1 17:19 gen1.sql.pt
-rw------- 1 root root 15677999 Jun  1 17:19 gen1.ques.pt
-rw------- 1 root root     6432 Jun  3 08:14 gen_gazp.csv
-rw------- 1 root root      151 Jun  3 08:17 gen_gazp.gsheet
-rw------- 1 root root 16564207 Jun  6 16:11 gen1.debug.pt
-rw------- 1 root root   942383 Jun  6 16:11 gen1.pt
-rw------- 1 root root     9861 Jun  6 16:11 gen1.json
-rw------- 1 root root 56523503 Jun  6 18:10 gen_pretrained.sql.pt
-rw------- 1 root root 64895535 Jun  6 18:10 gen_pretrained.ques.pt
-rw------- 1 root root 27943023 Jun  6 19:07 gen_pretrained.pt
-rw------- 1 root root   402421 Jun  6 19:07 gen_pretrained.json
-rw------- 1 root root   287812 Jun  6 19:24 gen_pretrained.csv
-rw------- 1 root root      151 Jun  7 05:51 gen_pretrained.gsheet
-rw------- 1 root root  5518319 Jul  6 19:56 gen_bert.sql.pt
-rw------- 1 root root  7784239 Jul  6 19:56 gen_bert.ques.pt
-rw------- 1 root root  8317935 Jul  6 20:02 gen_bert.debug.pt
-rw---

In [ ]:
#!mkdir gen
!python generate.py --dataset cosql --num 500  --resume "/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/exp/sql2nl/r1/best.tar" --fout "/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/gen/gen_bert.json"  --fparser "/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/exp/nl2sql/r1/best.tar"

2021-07-06 19:50:53.137833: I tensorflow/stream_executor/platform/default/dso_loader.cc:53] Successfully opened dynamic library libcudart.so.11.0
Namespace(aug='ans2sql', batch=20, beam_size=0, dataset='cosql', db='/content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp/data/database', db_split='eval', dcache='cache/bert', debug=False, dexp='exp', epoch=50, fout='/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/gen/gen_bert.json', fparser='/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/exp/nl2sql/r1/best.tar', ftrain='/content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp/data/spider/train.json', gpu=True, lr=5e-05, max_grad_norm=20, max_query_len=50, max_value_len=20, model='sql2nl', n_proc=1, name='default', num_gen=500, restart_optim=False, restart_scheduler=False, resume='/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/exp/sql2nl/r1/best.tar', seed=3, skip_consistency_check=False, skip_intermediate=False, tables='/content/

# Evaluation

In [ ]:
!ls -ltr

total 225
-rw------- 1 root root  2967 Feb  1 12:49 utils.py
-rw------- 1 root root  3378 Feb  1 12:49 timed_execute.py
-rw------- 1 root root  4830 Feb  1 12:49 README.md
-rw------- 1 root root  8291 Feb  1 12:49 preprocess_sql2nl_sparc.py
-rw------- 1 root root  9725 Feb  1 12:49 preprocess_nl2sql_sparc.py
-rw------- 1 root root 14555 Feb  1 12:49 preprocess_nl2sql_novalue.py
-rw------- 1 root root  3652 Feb  1 12:49 predict.py
-rw------- 1 root root  1069 Feb  1 12:49 LICENSE
-rw------- 1 root root 17672 Feb  1 12:49 editsql_postprocess.py
-rw------- 1 root root   379 Feb  1 12:49 download.sh
-rw------- 1 root root   234 Feb  1 12:49 download_nltk.py
-rw------- 1 root root  4083 Feb  1 12:49 dataset.py
-rw------- 1 root root 28125 Feb  1 12:49 bleu.py
drwx------ 2 root root  4096 May 10 12:35 model
drwx------ 2 root root  4096 May 10 12:35 eval_scripts
drwx------ 2 root root  4096 May 10 12:35 adapt
drwx------ 4 root root  4096 May 10 12:36 data
drwx------ 3 root root  4096 May 10 1

In [ ]:
!sh pred.sh "r1" './data/cosql'

+ name=r1
+ data=./data/cosql
+ root=exp/nl2sql/r1
+ fpred=exp/nl2sql/r1/dev_pred.txt
+ feval=exp/nl2sql/r1/dev_eval.txt
+ ftest=exp/nl2sql/r1/dev_scores.txt
+ python predict_sparc.py exp/nl2sql/r1/best.tar ./data/cosql/dev.json --tables ./data/cosql/tables.json --db data/database --dcache cache/bert --output exp/nl2sql/r1/dev_pred.txt
2021-07-16 21:39:41.069996: I tensorflow/stream_executor/platform/default/dso_loader.cc:53] Successfully opened dynamic library libcudart.so.11.0
/content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp/data/database
/content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp/data/cosql/tables.json
/content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp/data/database
/content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp/data/cosql/tables.json
Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated
Some weights of the model checkpoint a

In [ ]:
#!mkdir gen
#!python generate.py --dataset cosql --num 500  --resume "/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/exp/sql2nl/r1/best.tar" --fout "/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/gen/gen_bert.json"  --fparser "/content/drive/MyDrive/Colab Notebooks/NL_2_SQL/gazp/exp/nl2sql/r1/best.tar"

# New Section

In [ ]:
!python train.py --test_only --dataset cosql --drnn 300 --keep_values --model nl2sql --resume "/content/drive/My Drive/NL2SQL/Models/gazp/exp/nl2sql/r1/cosql_nl2sql.tar"

2021-06-06 14:57:07.617522: I tensorflow/stream_executor/platform/default/dso_loader.cc:53] Successfully opened dynamic library libcudart.so.11.0
cache/data_nl2sql_cosql.pt
pruned length from 6459 to 6215
/content/drive/My Drive/NL2SQL/Models/gazp/data/database
/content/drive/My Drive/NL2SQL/Models/gazp/data/spider/tables.json
/content/drive/My Drive/NL2SQL/Models/gazp/data/database
/content/drive/My Drive/NL2SQL/Models/gazp/data/spider/tables.json
/usr/local/lib/python3.7/dist-packages/transformers/tokenization_utils_base.py:1631: FutureWarning: Calling DistilBertTokenizer.from_pretrained() with the path to a single file or url is deprecated and won't be possible anymore in v5. Use a model identifier or the path to a directory instead.
  FutureWarning,
Some weights of the model checkpoint at cache/bert were not used when initializing DistilBertModel: ['vocab_projector.bias', 'vocab_layer_norm.bias', 'vocab_transform.bias', 'vocab_transform.weight', 'vocab_layer_norm.weight', 'vocab_pr

In [ ]:
#!mkdir gen
!python generate.py --dataset cosql --num 1000  --resume "/content/drive/My Drive/NL2SQL/Models/gazp/exp/sql2nl/r1/cosql_sql2nl.tar" --fout "/content/drive/My Drive/NL2SQL/Models/gazp/gen/gen_pretrained.json"  --fparser "/content/drive/My Drive/NL2SQL/Models/gazp/exp/nl2sql/r1/cosql_nl2sql.tar" --ftrain "/content/drive/My Drive/NL2SQL/Models/gazp/data/cosql/train.json"

Streaming output truncated to the last 5000 lines.
db: /content/drive/My Drive/NL2SQL/Models/gazp/data/database/voter_1/voter_1.sqlite
/content/drive/My Drive/NL2SQL/Models/gazp/data/database/voter_1/voter_1.sqlite
db: /content/drive/My Drive/NL2SQL/Models/gazp/data/database/voter_1/voter_1.sqlite
official eval:  69% 2707/3942 [13:35<05:58,  3.45it/s]/content/drive/My Drive/NL2SQL/Models/gazp/data/database/dog_kennels/dog_kennels.sqlite
db: /content/drive/My Drive/NL2SQL/Models/gazp/data/database/dog_kennels/dog_kennels.sqlite
/content/drive/My Drive/NL2SQL/Models/gazp/data/database/dog_kennels/dog_kennels.sqlite
db: /content/drive/My Drive/NL2SQL/Models/gazp/data/database/dog_kennels/dog_kennels.sqlite
official eval:  69% 2708/3942 [13:36<06:08,  3.35it/s]/content/drive/My Drive/NL2SQL/Models/gazp/data/database/pets_1/pets_1.sqlite
db: /content/drive/My Drive/NL2SQL/Models/gazp/data/database/pets_1/pets_1.sqlite
/content/drive/My Drive/NL2SQL/Models/gazp/data/database/pets_1/pets_1.sq

In [ ]:
sqltnsr = torch.load("/content/drive/My Drive/NL2SQL/Models/gazp/gen/gen_pretrained.sql.pt")
questiontnsr = torch.load("/content/drive/My Drive/NL2SQL/Models/gazp/gen/gen_pretrained.ques.pt")
alltnsr = torch.load("/content/drive/My Drive/NL2SQL/Models/gazp/gen/gen_pretrained.pt")

In [ ]:
for x in sqltnsr:
  print(x)
  break;

{'id': 'gen:0', 'columns': [{'oname': '*', 'name': '*', 'type': 'all', 'key': 'battle.*', 'table_name': 'battle'}, {'oname': 'id', 'name': 'id', 'type': 'key', 'key': 'battle.id', 'table_name': 'battle'}, {'oname': 'name', 'name': 'name', 'type': 'text', 'key': 'battle.name', 'table_name': 'battle'}, {'oname': 'date', 'name': 'date', 'type': 'text', 'key': 'battle.date', 'table_name': 'battle'}, {'oname': 'bulgarian_commander', 'name': 'bulgarian commander', 'type': 'text', 'key': 'battle.bulgarian_commander', 'table_name': 'battle'}, {'oname': 'latin_commander', 'name': 'latin commander', 'type': 'text', 'key': 'battle.latin_commander', 'table_name': 'battle'}, {'oname': 'result', 'name': 'result', 'type': 'text', 'key': 'battle.result', 'table_name': 'battle'}, {'oname': '*', 'name': '*', 'type': 'all', 'key': 'ship.*', 'table_name': 'ship'}, {'oname': 'lost_in_battle', 'name': 'lost in battle', 'type': 'key', 'key': 'ship.lost_in_battle', 'table_name': 'ship'}, {'oname': 'id', 'name

In [ ]:
for x in questiontnsr:
  print(x)
  break;

{'id': 'gen:0', 'columns': [{'oname': '*', 'name': '*', 'type': 'all', 'key': 'battle.*', 'table_name': 'battle'}, {'oname': 'id', 'name': 'id', 'type': 'key', 'key': 'battle.id', 'table_name': 'battle'}, {'oname': 'name', 'name': 'name', 'type': 'text', 'key': 'battle.name', 'table_name': 'battle'}, {'oname': 'date', 'name': 'date', 'type': 'text', 'key': 'battle.date', 'table_name': 'battle'}, {'oname': 'bulgarian_commander', 'name': 'bulgarian commander', 'type': 'text', 'key': 'battle.bulgarian_commander', 'table_name': 'battle'}, {'oname': 'latin_commander', 'name': 'latin commander', 'type': 'text', 'key': 'battle.latin_commander', 'table_name': 'battle'}, {'oname': 'result', 'name': 'result', 'type': 'text', 'key': 'battle.result', 'table_name': 'battle'}, {'oname': '*', 'name': '*', 'type': 'all', 'key': 'ship.*', 'table_name': 'ship'}, {'oname': 'lost_in_battle', 'name': 'lost in battle', 'type': 'key', 'key': 'ship.lost_in_battle', 'table_name': 'ship'}, {'oname': 'id', 'name

In [ ]:
for x in alltnsr:
  print(x)
  break;

{'id': 'gen:7', 'columns': [{'oname': '*', 'name': '*', 'type': 'all', 'key': 'employee.*', 'table_name': 'employee'}, {'oname': 'Employee_ID', 'name': 'employee id', 'type': 'key', 'key': 'employee.employee_id', 'table_name': 'employee'}, {'oname': 'Name', 'name': 'name', 'type': 'text', 'key': 'employee.name', 'table_name': 'employee'}, {'oname': 'Age', 'name': 'age', 'type': 'number', 'key': 'employee.age', 'table_name': 'employee'}, {'oname': 'City', 'name': 'city', 'type': 'text', 'key': 'employee.city', 'table_name': 'employee'}, {'oname': '*', 'name': '*', 'type': 'all', 'key': 'shop.*', 'table_name': 'shop'}, {'oname': 'Shop_ID', 'name': 'shop id', 'type': 'key', 'key': 'shop.shop_id', 'table_name': 'shop'}, {'oname': 'Name', 'name': 'name', 'type': 'text', 'key': 'shop.name', 'table_name': 'shop'}, {'oname': 'Location', 'name': 'location', 'type': 'text', 'key': 'shop.location', 'table_name': 'shop'}, {'oname': 'District', 'name': 'district', 'type': 'text', 'key': 'shop.distr

# New Section

In [ ]:
!python preprocess_nl2sql.py

In [ ]:
!python preprocess_sql2nl.py

In [ ]:
!pwd

In [ ]:
!python train.py --dataset spider --name r1 --keep_values --model nl2sql

In [ ]:
!python train.py --dataset spider --name r1 --keep_values --model nl2sql

In [ ]:
!python train.py --dataset cosql --name r1 --model sql2nl --fparser "/content/drive/My Drive/NL2SQL/Models/gazp/exp/sql2nl/r1/best.tar" --fcache "/content/drive/My Drive/NL2SQL/Models/gazp/cache/data_sql2nl_sparc_cosql.pt"

In [ ]:
#conn = sqlite3.connect("/content/drive/My Drive/NL2SQL/Models/gazp/data/database/department_management/department_management.sqlite")

In [ ]:
#conn.close()

In [ ]:
!python preprocess_nl2sql_cosql.py

In [ ]:
!python preprocess_sql2nl_cosql.py

In [ ]:
#!mkdir gen
!python generate.py --dataset cosql --num 1000  --resume "/content/drive/My Drive/NL2SQL/Models/gazp/exp/sql2nl/r1/best.tar" --fout "/content/drive/My Drive/NL2SQL/Models/gazp/gen/gen1.json"  --fparser "/content/drive/My Drive/NL2SQL/Models/gazp/exp/nl2sql/r1/best.tar"

2021-07-06 20:02:48.647162: I tensorflow/stream_executor/platform/default/dso_loader.cc:53] Successfully opened dynamic library libcudart.so.11.0
Namespace(aug='ans2sql', batch=20, beam_size=0, dataset='cosql', db='/content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp/data/database', db_split='eval', dcache='cache/bert', debug=False, dexp='exp', epoch=50, fout='/content/drive/My Drive/NL2SQL/Models/gazp/gen/gen1.json', fparser='/content/drive/My Drive/NL2SQL/Models/gazp/exp/nl2sql/r1/best.tar', ftrain='/content/drive/.shortcut-targets-by-id/1jcvivH0SB9ib1BwkwkXHJD_QWAnQFT0P/gazp/data/spider/train.json', gpu=True, lr=5e-05, max_grad_norm=20, max_query_len=50, max_value_len=20, model='sql2nl', n_proc=1, name='default', num_gen=1000, restart_optim=False, restart_scheduler=False, resume='/content/drive/My Drive/NL2SQL/Models/gazp/exp/sql2nl/r1/best.tar', seed=3, skip_consistency_check=False, skip_intermediate=False, tables='/content/drive/.shortcut-targets-by-id/1jc

In [ ]:
!python predict.py  --dataset=cosql

In [ ]:
!python predict.py "/content/drive/My Drive/NL2SQL/Models/gazp/exp/sql2nl/r1/best.tar" "/content/drive/My Drive/NL2SQL/Models/gazp/data/dev.json" --tables "/content/drive/My Drive/NL2SQL/Models/gazp/data/tables.json" --db "/content/drive/My Drive/NL2SQL/Models/gazp/data/database" --dcache "/content/drive/My Drive/NL2SQL/Models/gazp/cache/bert" --output "/content/drive/My Drive/NL2SQL/Models/gazp/exp/nl2sql/r1/scores.txt"


2021-06-03 08:55:35.291379: I tensorflow/stream_executor/platform/default/dso_loader.cc:53] Successfully opened dynamic library libcudart.so.11.0
^C


In [ ]:
!ls -ltr